In [ ]:
import os
import pandas as pd
from tqdm import tqdm
import datetime 
import numpy as np
import scipy.stats
import pymannkendall as mk
import matplotlib.pyplot as plt
from scipy.interpolate import make_interp_spline
import math
import jenkspy

In [ ]:
DATA_PATH = '../data'

## Data Audit

IRT Data

In [ ]:
IRT_PATH = os.path.join(DATA_PATH, 'IRT')
files_list = os.listdir(IRT_PATH)
print(f'There are {len(files_list)} files in IRT')

In [ ]:
df = {}
for file in tqdm(files_list):
    df[file] = pd.read_csv(os.path.join(IRT_PATH, file), low_memory=False,
                          usecols = ['date_created', 'sbg_gbg(agg)', 'case_channel', 'fb_market', 'market_region',
                                     'issue_category', 'issue_sub_category', 'l1_tag', 'l2_tag', 'l3_tag',
                                     'program', 'reporting_language', 'revenue_segment', 'service_lan',
                                     'Sum Res = Yes', 'tht_chat', 'irt_chat_sla', 'irt_email_sla',
                                     'Count Of Responses', 'cases created', 'owner', 'owner_tenure'])

In [ ]:
features = []
ref = []
diff = {}
for key, value in df.items():
    if not ref:
        ref = set(value.columns)
    else:
        diff = ref.symmetric_difference(set(value.columns))
    
    if diff:
        raise TypeError('Columns are different')
    
print(f'List of features: {ref}')
print(f'Number of features: {len(ref)}')

There are consistent features across files.

In [ ]:
df_IRT = pd.DataFrame()
for key, value in df.items():
    df_IRT = pd.concat([df_IRT, value])

In [ ]:
df_IRT.head(5)

In [ ]:
df_IRT.shape

In [ ]:
null_percentage = pd.DataFrame(
    (100 * df_IRT.isna().sum() / df_IRT.shape[0]).sort_values(ascending=False),
     columns=['Percentage'])

display(null_percentage)
num_null = len(null_percentage[null_percentage.Percentage != 0])
print(f'Number of features with null values: {num_null}')

In [ ]:
dup = df_IRT.shape[0] - df_IRT.drop_duplicates().shape[0]
print(f'There are {dup} duplicate rows')

In [ ]:
df_IRT = df_IRT.drop_duplicates()

Masterfile Data

In [ ]:
df_masterfile = pd.read_csv('../data/Active_Inactive_Agents.csv')

In [ ]:
df_masterfile.head(5)

In [ ]:
df_masterfile.shape

In [ ]:
dup = df_masterfile.shape[0] - df_masterfile.drop_duplicates().shape[0]
print(f'There are {dup} duplicate rows')

## Data Prep

In [ ]:
df_IRT.columns = df_IRT.columns.str.replace(' ', '_')

In [ ]:
df_IRT = df_IRT.rename(columns = {'Sum_Res_=_Yes': 'Sum_Res_Yes'})

In [ ]:
df_IRT['owner'] = df_IRT['owner'].astype('str')

In [ ]:
df_masterfile['SRTRepID'] = df_masterfile['SRTRepID'].astype('str')

In [ ]:
df_IRT = df_IRT.merge(df_masterfile[['SRTRepID', 'Hired Date']],
                    how = "left", left_on = 'owner', right_on = 'SRTRepID' )

In [ ]:
df_IRT['date_created'] = pd.to_datetime(df_IRT['date_created'])

In [ ]:
df_IRT['date_created'].min(), df_IRT['date_created'].max()

In [ ]:
df_IRT['created_month_year'] = df_IRT['date_created'].dt.to_period('M')

In [ ]:
df_IRT['created_year'] = df_IRT['date_created'].dt.to_period('Y')

In [ ]:
df_IRT['Hired Date'] = pd.to_datetime(df_IRT['Hired Date'])

In [ ]:
df_IRT['hired_month_year'] = df_IRT['Hired Date'].dt.to_period('M')

In [ ]:
df_IRT['hired_year'] = df_IRT['Hired Date'].dt.to_period('Y').astype('str')

In [ ]:
df_IRT['Tenure'] = ((df_IRT['date_created'] - df_IRT['Hired Date'])/np.timedelta64(1, 'M'))
df_IRT['Tenure'] = np.floor(pd.to_numeric(df_IRT['Tenure'], errors='coerce')).astype('Int64') + 1

# Learning Curve (General) 

- KPI computation

In [ ]:
kpi = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
             (df_IRT['program'] == "Advertiser Concierge") &
             (df_IRT['Tenure'] >= 1) &
             (df_IRT['Tenure'] <= 18)].groupby(['Tenure']).aggregate(
    rr_yes = ('Sum_Res_Yes', 'sum'),
    survey_count = ('Count_Of_Responses', 'sum'),
    THT_chat = ('tht_chat', 'sum'),
    irt_chat_sla = ('irt_chat_sla', 'sum'),
    irt_email_sla = ('irt_email_sla', 'sum')).reset_index()

In [ ]:
chat_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                    (df_IRT['program'] == "Advertiser Concierge") &
                    (df_IRT['case_channel'] == "CHAT") &
                    (df_IRT['Tenure'] >= 1) &
                    (df_IRT['Tenure'] <= 18)].groupby(['Tenure']).aggregate(
    chat_count = ('cases_created', 'sum')).reset_index()

In [ ]:
email_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                     (df_IRT['program'] == "Advertiser Concierge") &
                     (df_IRT['case_channel'] == "EMAIL") &
                     (df_IRT['Tenure'] >= 1) &
                     (df_IRT['Tenure'] <= 18)].groupby(['Tenure']).aggregate(
    email_count = ('cases_created', 'sum')).reset_index()

In [ ]:
kpi = kpi.merge(chat_count, how = "left", on = "Tenure")
kpi = kpi.merge(email_count, how = "left", on = "Tenure")

In [ ]:
kpi['RR'] = kpi['rr_yes']/ kpi['survey_count']
kpi['AHT'] = (kpi['THT_chat']/60)/ kpi['chat_count']
kpi['Chat SLA'] = kpi['irt_chat_sla']/ kpi['chat_count']
kpi['Email SLA'] = kpi['irt_email_sla']/ kpi['email_count']

In [ ]:
pd.options.display.max_rows = None
kpi

In [ ]:
metric = ['RR', 'AHT', 'Chat SLA', 'Email SLA']
increasing_metric = ['RR', 'Chat SLA', 'Email SLA']
decreasing_metric = ['AHT']

- Check Trend

In [ ]:
kpi_trend = pd.DataFrame(columns = ['KPI', 'Volume', 'Trend', 'Statistic', 'pvalue'])

In [ ]:
for i in range(len(metric)):
    kpi_interest = metric[i]
    
    if kpi_interest == "RR":
        df_interest = kpi[['Tenure', 'survey_count', kpi_interest]]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        count = df_interest['survey_count'].sum()
        
        mk_test = mk.original_test(df_interest[kpi_interest])
        trend = mk_test.trend
        zstatistic = mk_test.z
        pvalue = mk_test.p
        kpi_trend.loc[len(kpi_trend.index)] = [kpi_interest, count, trend, zstatistic, pvalue]
    
    elif kpi_interest == "Email SLA":
        df_interest = kpi[['Tenure', 'email_count', kpi_interest]]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        count = df_interest['email_count'].sum()
        
        mk_test = mk.original_test(df_interest[kpi_interest])
        trend = mk_test.trend
        zstatistic = mk_test.z
        pvalue = mk_test.p
        kpi_trend.loc[len(kpi_trend.index)] = [kpi_interest, count, trend, zstatistic, pvalue]
            
    else:
        df_interest = kpi[['Tenure', 'chat_count', kpi_interest]]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        count = df_interest['chat_count'].sum()
        
        mk_test = mk.original_test(df_interest[kpi_interest])
        trend = mk_test.trend
        zstatistic = mk_test.z
        pvalue = mk_test.p
        kpi_trend.loc[len(kpi_trend.index)] = [kpi_interest, count, trend, zstatistic, pvalue]

In [ ]:
kpi_trend.loc[(kpi_trend['Trend'] == "no trend") &
              (kpi_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') < 0) &
              (kpi_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "decreasing"

kpi_trend.loc[(kpi_trend['Trend'] == "no trend") &
              (kpi_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') > 0) &
              (kpi_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "increasing"

In [ ]:
kpi_trend

- Get Learning Curve

In [ ]:
KPI_learningcurve = pd.DataFrame(columns = ['Metric', 'Volume', 'Average Perfomance', 'Trend', 'Learning Curve'])

In [ ]:
for i in range(len(metric)):
    kpi_interest = metric[i]
    df_interest = kpi
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        
    if kpi_interest == "RR":
        count = df_interest['survey_count'].sum()
    elif kpi_interest == "Email SLA":
        count = df_interest['email_count'].sum()
    else:
        count = df_interest['chat_count'].sum()
        
    df_interest = df_interest[(df_interest['Tenure'] > 1)][['Tenure', kpi_interest]]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    
    trend = kpi_trend.loc[(kpi_trend['KPI'] == kpi_interest), "Trend"].iloc[0]
    ave = df_interest[kpi_interest].describe()["mean"]
        
    if ((kpi_interest in increasing_metric) &
        (trend == "increasing")):
        
        curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
        for index in df_interest.index:
            if df_interest.loc[index, kpi_interest] > ave:
                curve = df_interest.loc[index, 'Tenure']
                break
        
        KPI_learningcurve.loc[len(KPI_learningcurve.index)] = [kpi_interest, count, ave, trend, curve]
            
    elif ((kpi_interest in decreasing_metric) &
          (trend == "decreasing")):
        
        curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
        for index in df_interest.index:
            if df_interest.loc[index, kpi_interest] < ave:
                curve = df_interest.loc[index, 'Tenure']
                break
        KPI_learningcurve.loc[len(KPI_learningcurve.index)] = [kpi_interest, count, ave, trend, curve]
            
    else:
        KPI_learningcurve.loc[len(KPI_learningcurve.index)] = [kpi_interest, count, ave, trend, "Not Applicable"]

In [ ]:
KPI_learningcurve

- KPI Graph

In [ ]:
kpi_interest = "RR"
df_interest = kpi[['Tenure', 'survey_count', kpi_interest]]
df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    
fig, ax1 = plt.subplots(figsize = (8, 5))
target = 0.71
ave = df_interest[(df_interest['Tenure'] > 1)][kpi_interest].describe()["mean"]

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax1.plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
ax1.set_xlabel("Tenure (in Months)")
ax1.set_ylabel("Resolution Rate")

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['survey_count'])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax2 = ax1.twinx()
ax2.plot(X_, Y_, 'gray', linewidth = 2)
ax2.set_ylabel("Survey Count")

ax1.hlines(y = target, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'red', linestyle = 'dashed', label = "Target")
ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'black', linestyle = 'dashed', label = "Mean")

ax1.set_title(label = "Resolution Rate", fontweight = "bold", loc = "left", color = "black")
ax1.legend(loc = "best")
ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        
plt.show()

In [ ]:
kpi_interest = "AHT"
df_interest = kpi[['Tenure', 'chat_count', kpi_interest]]
df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    
fig, ax1 = plt.subplots(figsize = (8, 5))
target = 22
ave = df_interest[(df_interest['Tenure'] > 1)][kpi_interest].describe()["mean"]

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax1.plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
ax1.set_xlabel("Tenure (in Months)")
ax1.set_ylabel("Average Handle Time (Chat)")

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['chat_count'])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax2 = ax1.twinx()
ax2.plot(X_, Y_, 'gray', linewidth = 2)
ax2.set_ylabel("Chat Count")

ax1.hlines(y = target, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'red', linestyle = 'dashed', label = "Target")
ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'black', linestyle = 'dashed', label = "Mean")

ax1.set_title(label = "Average Handle Time (Chat)", fontweight = "bold", loc = "left", color = "black")
ax1.legend(loc = "best")
ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        
plt.show()

In [ ]:
kpi_interest = "Chat SLA"
df_interest = kpi[['Tenure', 'chat_count', kpi_interest]]
df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    
fig, ax1 = plt.subplots(figsize = (8, 5))
target = 0.80
ave = df_interest[(df_interest['Tenure'] > 1)][kpi_interest].describe()["mean"]

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax1.plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
ax1.set_xlabel("Tenure (in Months)")
ax1.set_ylabel("Chat SLA")

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['chat_count'])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax2 = ax1.twinx()
ax2.plot(X_, Y_, 'gray', linewidth = 2)
ax2.set_ylabel("Chat Count")

ax1.hlines(y = target, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'red', linestyle = 'dashed', label = "Target")
ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'black', linestyle = 'dashed', label = "Mean")

ax1.set_title(label = "Chat SLA", fontweight = "bold", loc = "left", color = "black")
ax1.legend(loc = "best")
ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        
plt.show()

In [ ]:
kpi_interest = "Email SLA"
df_interest = kpi[['Tenure', 'email_count', kpi_interest]]
df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    
fig, ax1 = plt.subplots(figsize = (8, 5))
target = 0.80
ave = df_interest[(df_interest['Tenure'] > 1)][kpi_interest].describe()["mean"]

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax1.plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
ax1.set_xlabel("Tenure (in Months)")
ax1.set_ylabel("Email SLA")

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['email_count'])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax2 = ax1.twinx()
ax2.plot(X_, Y_, 'gray', linewidth = 2)
ax2.set_ylabel("Email Count")

ax1.hlines(y = target, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'red', linestyle = 'dashed', label = "Target")
ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'black', linestyle = 'dashed', label = "Mean")

ax1.set_title(label = "Email SLA", fontweight = "bold", loc = "left", color = "black")
ax1.legend(loc = "best")
ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        
plt.show()

# Learning Curve (Year) 

- KPI computation

In [ ]:
year = ['2021', '2022', '2023']

In [ ]:
year_kpi = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                  (df_IRT['program'] == "Advertiser Concierge") &
                  (df_IRT['hired_year'].isin(year)) &
                  (df_IRT['Tenure'] >= 1) &
                  (df_IRT['Tenure'] <= 18)].groupby(['hired_year', 'Tenure']).aggregate(
    rr_yes = ('Sum_Res_Yes', 'sum'),
    survey_count = ('Count_Of_Responses', 'sum'),
    THT_chat = ('tht_chat', 'sum'),
    irt_chat_sla = ('irt_chat_sla', 'sum'),
    irt_email_sla = ('irt_email_sla', 'sum')).reset_index()

In [ ]:
chat_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                    (df_IRT['program'] == "Advertiser Concierge") &
                    (df_IRT['case_channel'] == "CHAT") &
                    (df_IRT['hired_year'].isin(year)) &
                    (df_IRT['Tenure'] >= 1) &
                    (df_IRT['Tenure'] <= 18)].groupby(['hired_year','Tenure']).aggregate(
    chat_count = ('cases_created', 'sum')).reset_index()

In [ ]:
email_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                     (df_IRT['program'] == "Advertiser Concierge") &
                     (df_IRT['case_channel'] == "EMAIL") & 
                     (df_IRT['hired_year'].isin(year)) &
                     (df_IRT['Tenure'] >= 1) &
                     (df_IRT['Tenure'] <= 18)].groupby(['hired_year','Tenure']).aggregate(
    email_count = ('cases_created', 'sum')).reset_index()

In [ ]:
year_kpi = year_kpi.merge(chat_count, how = "left", on = ["hired_year", "Tenure"])
year_kpi = year_kpi.merge(email_count, how = "left", on = ["hired_year", "Tenure"])

In [ ]:
year_kpi['RR'] = year_kpi['rr_yes']/ year_kpi['survey_count']
year_kpi['AHT'] = (year_kpi['THT_chat']/60)/ year_kpi['chat_count']
year_kpi['Chat SLA'] = year_kpi['irt_chat_sla']/ year_kpi['chat_count']
year_kpi['Email SLA'] = year_kpi['irt_email_sla']/ year_kpi['email_count']

In [ ]:
pd.options.display.max_rows = None
year_kpi

- Check Trend

In [ ]:
year_trend = pd.DataFrame(columns = ['Year', 'KPI', 'Volume', 'Trend', 'Statistic', 'pvalue'])

In [ ]:
for j in range(len(year)):
    for i in range(len(metric)):
        kpi_interest = metric[i]
    
        if kpi_interest == "RR":
            df_interest = year_kpi[year_kpi['hired_year'] == year[j]][['Tenure', 'survey_count', kpi_interest]]
            df_interest = df_interest[~(df_interest[kpi_interest].isna())]
            count = df_interest['survey_count'].sum()
        
            mk_test = mk.original_test(df_interest[kpi_interest])
            trend = mk_test.trend
            zstatistic = mk_test.z
            pvalue = mk_test.p
            year_trend.loc[len(year_trend.index)] = [year[j], kpi_interest, count, trend, zstatistic, pvalue]
        
        elif kpi_interest == "Email SLA":
            df_interest = year_kpi[year_kpi['hired_year'] == year[j]][['Tenure', 'email_count', kpi_interest]]
            df_interest = df_interest[~(df_interest[kpi_interest].isna())]
            count = df_interest['email_count'].sum()
        
            mk_test = mk.original_test(df_interest[kpi_interest])
            trend = mk_test.trend
            zstatistic = mk_test.z
            pvalue = mk_test.p
            year_trend.loc[len(year_trend.index)] = [year[j], kpi_interest, count, trend, zstatistic, pvalue]
            
        else:
            df_interest = year_kpi[year_kpi['hired_year'] == year[j]][['Tenure', 'chat_count', kpi_interest]]
            df_interest = df_interest[~(df_interest[kpi_interest].isna())]
            count = df_interest['chat_count'].sum()
        
            mk_test = mk.original_test(df_interest[kpi_interest])
            trend = mk_test.trend
            zstatistic = mk_test.z
            pvalue = mk_test.p
            year_trend.loc[len(year_trend.index)] = [year[j], kpi_interest, count, trend, zstatistic, pvalue]

In [ ]:
year_trend.loc[(year_trend['Trend'] == "no trend") &
              (year_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') < 0) &
              (year_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "decreasing"

year_trend.loc[(year_trend['Trend'] == "no trend") &
              (year_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') > 0) &
              (year_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "increasing"

In [ ]:
year_trend

- Get Learning Curve

In [ ]:
year_learningcurve = pd.DataFrame(columns = ['Year', 'Metric', 'Volume', 'Average Perfomance', 'Trend', 'Learning Curve'])

In [ ]:
for i in range(len(year)):
    for j in range(len(metric)):
        year_interest = year[i]
        kpi_interest = metric[j]
        
        df_interest = year_kpi[(year_kpi['hired_year'] == year_interest)]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        
        if kpi_interest == "RR":
            count = df_interest['survey_count'].sum()
        elif kpi_interest == "Email SLA":
            count = df_interest['email_count'].sum()
        else:
            count = df_interest['chat_count'].sum()
        
        df_interest = df_interest[(df_interest['Tenure'] > 1)][['Tenure', kpi_interest]]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        
        trend = year_trend.loc[(year_trend['Year'] == year_interest) &
                               (year_trend['KPI'] == kpi_interest), "Trend"].iloc[0]
        ave = df_interest[kpi_interest].describe()["mean"]
        
        if ((kpi_interest in increasing_metric) &
            (trend == "increasing")):
            
            curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
            for index in df_interest.index:
                if df_interest.loc[index, kpi_interest] > ave:
                    curve = df_interest.loc[index, 'Tenure']
                    break
            year_learningcurve.loc[len(year_learningcurve.index)] = [year_interest, kpi_interest, count,
                                                                     ave, trend, curve]
            
        elif ((kpi_interest in decreasing_metric) &
              (trend == "decreasing")):
            
            curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
            for index in df_interest.index:
                if df_interest.loc[index, kpi_interest] < ave:
                    curve = df_interest.loc[index, 'Tenure']
                    break
            year_learningcurve.loc[len(year_learningcurve.index)] = [year_interest, kpi_interest, count,
                                                                     ave, trend, curve]
            
        else:
            year_learningcurve.loc[len(year_learningcurve.index)] = [year_interest, kpi_interest, count,
                                                                     ave, trend, "Not Applicable"]

In [ ]:
year_learningcurve

- KPI Graph

In [ ]:
check = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
               (df_IRT['program'] == "Advertiser Concierge") &
               (df_IRT['hired_year'].isin(year)) &
               (df_IRT['Tenure'] >= 1) &
               (df_IRT['Tenure'] <= 18)].groupby(['hired_year', 'Tenure']).aggregate(
    agent_count = ('owner', 'nunique')).reset_index()

In [ ]:
fig, ax1 = plt.subplots(figsize = (8, 5))

df_interest = check[check['hired_year'] == "2021"]
X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['agent_count'])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax1.plot(X_, Y_, 'green', linewidth = 2, label = "Agent Count (2021)")

df_interest = check[check['hired_year'] == "2022"]
X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['agent_count'])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax1.plot(X_, Y_, 'orange', linewidth = 2, label = "Agent Count (2022)")

df_interest = check[check['hired_year'] == "2023"]
X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['agent_count'])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax1.plot(X_, Y_, 'blue', linewidth = 2, label = "Agent Count (2023)")
    
ax1.set_title(label = "Agent Count", fontweight = "bold", loc = "left", color = "black")
ax1.set_xlabel("Tenure (in Months)")
ax1.set_ylabel("Agent Count")
ax1.legend(loc = "best")
ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        
plt.show()

In [ ]:
target = pd.DataFrame({'KPI' : ['RR', 'AHT', 'Chat SLA', 'Email SLA'],
                       'target' : [0.71, 22, 0.80, 0.80]})

In [ ]:
title = pd.DataFrame({'KPI' : ['RR', 'AHT', 'Chat SLA', 'Email SLA'],
                      'title' : ['Resolution Rate', 'Average Handle Time (Chat)', 'Chat SLA', 'Email SLA']})

In [ ]:
for i in range(len(metric)):
    kpi_interest = metric[i]
    fig, ax1 = plt.subplots(figsize = (8, 5))
    
    target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
    ax1.hlines(y = target_interest, xmin = 0, xmax = 19,
               color = 'red', linestyle = 'dashed', label = "Target " + kpi_interest)

    df_interest = year_kpi[year_kpi['hired_year'] == "2021"]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    ave = df_interest[(df_interest['Tenure'] > 1)][kpi_interest].describe()["mean"]
    X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
    X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
    Y_ = X_Y_Spline(X_)
    ax1.plot(X_, Y_, 'green', linewidth = 2, label = kpi_interest + "(2021)")
    ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
               xmax = df_interest['Tenure'].max(),
               color = 'green', linestyle = 'dashed')
    
    df_interest = year_kpi[year_kpi['hired_year'] == "2022"]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    ave = df_interest[(df_interest['Tenure'] > 3)][kpi_interest].describe()["mean"]
    X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
    X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
    Y_ = X_Y_Spline(X_)
    ax1.plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest + "(2022)")
    ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
               xmax = df_interest['Tenure'].max(),
               color = 'orange', linestyle = 'dashed')

    df_interest = year_kpi[year_kpi['hired_year'] == "2023"]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    ave = df_interest[(df_interest['Tenure'] > 3)][kpi_interest].describe()["mean"]
    X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
    X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
    Y_ = X_Y_Spline(X_)
    ax1.plot(X_, Y_, 'blue', linewidth = 2, label = kpi_interest + "(2023)")
    ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
               xmax = df_interest['Tenure'].max(),
               color = 'blue', linestyle = 'dashed')
    
    plt_label = title.loc[(title['KPI'] == kpi_interest), "title"].iloc[0]
    ax1.set_title(label = plt_label, fontweight = "bold", loc = "left", color = "black")
    ax1.set_xlabel("Tenure (in Months)")
    ax1.set_ylabel(plt_label)
    ax1.legend(loc = "best")
    ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        
    plt.show()

# Learning Curve (L1 Tag) 

- KPI computation

In [ ]:
L1_kpi = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                (df_IRT['program'] == "Advertiser Concierge") &
                (~df_IRT['l1_tag'].isnull()) &
                (df_IRT['Tenure'] >= 1) &
                (df_IRT['Tenure'] <= 18)].groupby(['l1_tag', 'Tenure']).aggregate(
    rr_yes = ('Sum_Res_Yes', 'sum'),
    survey_count = ('Count_Of_Responses', 'sum'),
    THT_chat = ('tht_chat', 'sum'),
    irt_chat_sla = ('irt_chat_sla', 'sum'),
    irt_email_sla = ('irt_email_sla', 'sum')).reset_index()

In [ ]:
chat_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                    (df_IRT['program'] == "Advertiser Concierge") &
                    (df_IRT['case_channel'] == "CHAT") &
                    (~df_IRT['l1_tag'].isnull()) &
                    (df_IRT['Tenure'] >= 1) &
                    (df_IRT['Tenure'] <= 18)].groupby(['l1_tag','Tenure']).aggregate(
    chat_count = ('cases_created', 'sum')).reset_index()

In [ ]:
email_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                     (df_IRT['program'] == "Advertiser Concierge") &
                     (df_IRT['case_channel'] == "EMAIL") & 
                     (~df_IRT['l1_tag'].isnull()) &
                     (df_IRT['Tenure'] >= 1) &
                     (df_IRT['Tenure'] <= 18)].groupby(['l1_tag','Tenure']).aggregate(
    email_count = ('cases_created', 'sum')).reset_index()

In [ ]:
L1_kpi = L1_kpi.merge(chat_count, how = "left", on = ["l1_tag", "Tenure"])
L1_kpi = L1_kpi.merge(email_count, how = "left", on = ["l1_tag", "Tenure"])

In [ ]:
L1_kpi['RR'] = L1_kpi['rr_yes']/ L1_kpi['survey_count']
L1_kpi['AHT'] = (L1_kpi['THT_chat']/60)/ L1_kpi['chat_count']
L1_kpi['Chat SLA'] = L1_kpi['irt_chat_sla']/ L1_kpi['chat_count']
L1_kpi['Email SLA'] = L1_kpi['irt_email_sla']/ L1_kpi['email_count']

In [ ]:
pd.options.display.max_rows = None
L1_kpi

- Check Trend

In [ ]:
tags = L1_kpi['l1_tag'].unique()

In [ ]:
L1_trend = pd.DataFrame(columns = ['L1 Tag', 'KPI', 'Volume', 'Trend', 'Statistic', 'pvalue'])

In [ ]:
for i in range(len(tags)):
    for j in range(len(metric)):
        tag_interest = tags[i]
        kpi_interest = metric[j]
        df_interest = L1_kpi[L1_kpi['l1_tag'] == tag_interest]
        
        if kpi_interest == "RR":
            count = df_interest['survey_count'].sum()
        elif kpi_interest == "Email SLA":
            count = df_interest['email_count'].sum()
        else:
            count = df_interest['chat_count'].sum()
            
        df_interest = df_interest[['Tenure', kpi_interest]]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    
        if len(df_interest) >= 5:
            mk_test = mk.original_test(df_interest[kpi_interest])
            trend = mk_test.trend
            zstatistic = mk_test.z
            pvalue = mk_test.p
            L1_trend.loc[len(L1_trend.index)] = [tag_interest, kpi_interest, count,
                                                 trend, zstatistic, pvalue]
            
        else:
            trend = "Not Applicable"
            zstatistic = "Not Applicable"
            pvalue = "Not Applicable"
            L1_trend.loc[len(L1_trend.index)] = [tag_interest, kpi_interest, count,
                                                 trend, zstatistic, pvalue]

In [ ]:
L1_trend.loc[(L1_trend['Trend'] == "no trend") &
              (L1_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') < 0) &
              (L1_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "decreasing"

L1_trend.loc[(L1_trend['Trend'] == "no trend") &
              (L1_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') > 0) &
              (L1_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "increasing"

In [ ]:
L1_trend

- Get Learning Curve

In [ ]:
L1_learningcurve = pd.DataFrame(columns = ['L1 Tag', 'Metric', 'Volume', 'Average Perfomance', 'Trend', 'Learning Curve'])

In [ ]:
for i in range(len(tags)):
    for j in range(len(metric)):
        tag_interest = tags[i]
        kpi_interest = metric[j]
        
        df_interest = L1_kpi[(L1_kpi['l1_tag'] == tag_interest)]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        
        if kpi_interest == "RR":
            count = df_interest['survey_count'].sum()
        elif kpi_interest == "Email SLA":
            count = df_interest['email_count'].sum()
        else:
            count = df_interest['chat_count'].sum()
        
        df_interest = df_interest[(df_interest['Tenure'] > 1)][['Tenure', kpi_interest]]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        
        trend = L1_trend.loc[(L1_trend['L1 Tag'] == tag_interest) &
                             (L1_trend['KPI'] == kpi_interest), "Trend"].iloc[0]
        team_ave = L1_kpi[kpi_interest].describe()["mean"]
        ave = df_interest[kpi_interest].describe()["mean"]
        
        if ((kpi_interest in increasing_metric) &
            (trend == "increasing")):
            
            curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
            for index in df_interest.index:
                if df_interest.loc[index, kpi_interest] > team_ave:
                    curve = df_interest.loc[index, 'Tenure']
                    break
            L1_learningcurve.loc[len(L1_learningcurve.index)] = [tag_interest, kpi_interest, count,
                                                                 ave, trend, curve]
            
        elif ((kpi_interest in decreasing_metric) &
              (trend == "decreasing")):
            
            curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
            for index in df_interest.index:
                if df_interest.loc[index, kpi_interest] < ave:
                    curve = df_interest.loc[index, 'Tenure']
                    break
            L1_learningcurve.loc[len(L1_learningcurve.index)] = [tag_interest, kpi_interest, count,
                                                                 ave, trend, curve]
            
        else:
            L1_learningcurve.loc[len(L1_learningcurve.index)] = [tag_interest, kpi_interest, count,
                                                                 ave, trend, "Not Applicable"]

In [ ]:
L1_learningcurve

In [ ]:
L1_learningcurve.to_csv('../results/All Trends (L1 Tags).csv', index = False)

- KPI Graph

In [ ]:
tags.sort()

In [ ]:
for i in range(len(tags)):
    kpi_interest = "RR"
    tag_interest = tags[i]
    fig, ax1 = plt.subplots(figsize = (8, 5))
    
    target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
    ax1.hlines(y = target_interest, xmin = 0, xmax = 19,
               color = 'red', linestyle = 'dashed', label = "Target " + kpi_interest)

    df_interest = L1_kpi[L1_kpi['l1_tag'] == tag_interest]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    ave = L1_kpi[(L1_kpi['Tenure'] > 1)][kpi_interest].describe()["mean"]
    
    if len(df_interest) >= 5:
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax1.plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
        ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
                   xmax = df_interest['Tenure'].max(),
                   color = 'orange', linestyle = 'dashed')
        
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['survey_count'])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax2 = ax1.twinx()
        ax2.plot(X_, Y_, 'gray', linewidth = 2)
        
        curve = L1_learningcurve.loc[(L1_learningcurve['Metric'] == kpi_interest) &
                                     (L1_learningcurve['L1 Tag'] == tag_interest), 'Learning Curve'].iloc[0]
        if curve != "Not Applicable":
            curve_KPI = df_interest.loc[df_interest['Tenure'] == curve, kpi_interest].iloc[0]
            coords = curve, curve_KPI
            ax1.annotate("Learning Curve: " + str(curve) + " month",
                         xy = coords, xytext = (10, 15),
                         textcoords = 'offset points', ha = 'left', va = 'bottom',
                         bbox = dict(boxstyle = 'round', pad = 0.5, fc = 'white'))
            ax1.scatter(curve, curve_KPI, marker = 'o', color = 'orange', s = 80)
        
        ax1.set_title(label = tag_interest, fontweight = "bold", loc = "left", color = "black")
        ax1.legend(loc = "best")
        ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        plt_label = title.loc[(title['KPI'] == kpi_interest), "title"].iloc[0]
        ax1.set_xlabel("Tenure (in Months)")
        ax2.set_xlabel("Survey Count")
        ax1.set_ylabel(plt_label)
        plt.show()

In [ ]:
for i in range(len(tags)):
    kpi_interest = "AHT"
    tag_interest = tags[i]
    fig, ax1 = plt.subplots(figsize = (8, 5))
    
    target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
    ax1.hlines(y = target_interest, xmin = 0, xmax = 19,
               color = 'red', linestyle = 'dashed', label = "Target " + kpi_interest)

    df_interest = L1_kpi[L1_kpi['l1_tag'] == tag_interest]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    ave = L1_kpi[(L1_kpi['Tenure'] > 1)][kpi_interest].describe()["mean"]
    
    if len(df_interest) >= 5:
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax1.plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
        ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
                   xmax = df_interest['Tenure'].max(),
                   color = 'orange', linestyle = 'dashed')
        
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['chat_count'])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax2 = ax1.twinx()
        ax2.plot(X_, Y_, 'gray', linewidth = 2)
        
        curve = L1_learningcurve.loc[(L1_learningcurve['Metric'] == kpi_interest) &
                                     (L1_learningcurve['L1 Tag'] == tag_interest), 'Learning Curve'].iloc[0]
        if curve != "Not Applicable":
            curve_KPI = df_interest.loc[df_interest['Tenure'] == curve, kpi_interest].iloc[0]
            coords = curve, curve_KPI
            ax1.annotate("Learning Curve: " + str(curve) + " month",
                         xy = coords, xytext = (10, 15),
                         textcoords = 'offset points', ha = 'left', va = 'bottom',
                         bbox = dict(boxstyle = 'round', pad = 0.5, fc = 'white'))
            ax1.scatter(curve, curve_KPI, marker = 'o', color = 'orange', s = 80)
        
        ax1.set_title(label = tag_interest, fontweight = "bold", loc = "left", color = "black")
        ax1.legend(loc = "best")
        ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        plt_label = title.loc[(title['KPI'] == kpi_interest), "title"].iloc[0]
        ax1.set_xlabel("Tenure (in Months)")
        ax2.set_xlabel("Chat Count")
        ax1.set_ylabel(plt_label)
        plt.show()

In [ ]:
for i in range(len(tags)):
    kpi_interest = "Chat SLA"
    tag_interest = tags[i]
    fig, ax1 = plt.subplots(figsize = (8, 5))
    
    target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
    ax1.hlines(y = target_interest, xmin = 0, xmax = 19,
               color = 'red', linestyle = 'dashed', label = "Target " + kpi_interest)

    df_interest = L1_kpi[L1_kpi['l1_tag'] == tag_interest]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    ave = L1_kpi[(L1_kpi['Tenure'] > 1)][kpi_interest].describe()["mean"]
    
    if len(df_interest) >= 5:
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax1.plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
        ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
                   xmax = df_interest['Tenure'].max(),
                   color = 'orange', linestyle = 'dashed')
        
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['chat_count'])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax2 = ax1.twinx()
        ax2.plot(X_, Y_, 'gray', linewidth = 2)
        
        curve = L1_learningcurve.loc[(L1_learningcurve['Metric'] == kpi_interest) &
                                     (L1_learningcurve['L1 Tag'] == tag_interest), 'Learning Curve'].iloc[0]
        if curve != "Not Applicable":
            curve_KPI = df_interest.loc[df_interest['Tenure'] == curve, kpi_interest].iloc[0]
            coords = curve, curve_KPI
            ax1.annotate("Learning Curve: " + str(curve) + " month",
                         xy = coords, xytext = (10, 15),
                         textcoords = 'offset points', ha = 'left', va = 'bottom',
                         bbox = dict(boxstyle = 'round', pad = 0.5, fc = 'white'))
            ax1.scatter(curve, curve_KPI, marker = 'o', color = 'orange', s = 80)
        
        ax1.set_title(label = tag_interest, fontweight = "bold", loc = "left", color = "black")
        ax1.legend(loc = "best")
        ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        plt_label = title.loc[(title['KPI'] == kpi_interest), "title"].iloc[0]
        ax1.set_xlabel("Tenure (in Months)")
        ax2.set_xlabel("Chat Count")
        ax1.set_ylabel(plt_label)
        plt.show()

In [ ]:
for i in range(len(tags)):
    kpi_interest = "Email SLA"
    tag_interest = tags[i]
    fig, ax1 = plt.subplots(figsize = (8, 5))
    
    target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
    ax1.hlines(y = target_interest, xmin = 0, xmax = 19,
               color = 'red', linestyle = 'dashed', label = "Target " + kpi_interest)

    df_interest = L1_kpi[L1_kpi['l1_tag'] == tag_interest]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    ave = L1_kpi[(L1_kpi['Tenure'] > 1)][kpi_interest].describe()["mean"]
    
    if len(df_interest) >= 5:
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax1.plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
        ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
                   xmax = df_interest['Tenure'].max(),
                   color = 'orange', linestyle = 'dashed')
        
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['email_count'])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax2 = ax1.twinx()
        ax2.plot(X_, Y_, 'gray', linewidth = 2)
        
        curve = L1_learningcurve.loc[(L1_learningcurve['Metric'] == kpi_interest) &
                                     (L1_learningcurve['L1 Tag'] == tag_interest), 'Learning Curve'].iloc[0]
        if curve != "Not Applicable":
            curve_KPI = df_interest.loc[df_interest['Tenure'] == curve, kpi_interest].iloc[0]
            coords = curve, curve_KPI
            ax1.annotate("Learning Curve: " + str(curve) + " month",
                         xy = coords, xytext = (10, 15),
                         textcoords = 'offset points', ha = 'left', va = 'bottom',
                         bbox = dict(boxstyle = 'round', pad = 0.5, fc = 'white'))
            ax1.scatter(curve, curve_KPI, marker = 'o', color = 'orange', s = 80)
        
        ax1.set_title(label = tag_interest, fontweight = "bold", loc = "left", color = "black")
        ax1.legend(loc = "best")
        ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        plt_label = title.loc[(title['KPI'] == kpi_interest), "title"].iloc[0]
        ax1.set_xlabel("Tenure (in Months)")
        ax2.set_xlabel("Email Count")
        ax1.set_ylabel(plt_label)
        plt.show()

# Learning Curve (L1 & L2 Tag) 

- Check Ticket Count

In [ ]:
check_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                     (df_IRT['program'] == "Advertiser Concierge") &
                     (df_IRT['case_channel'] == "CHAT") &
                     (~df_IRT['l1_tag'].isnull()) &
                     (~df_IRT['l2_tag'].isnull()) &
                     (df_IRT['Tenure'] >= 1) &
                     (df_IRT['Tenure'] <= 18)].groupby(['l1_tag', 'l2_tag']).aggregate(
    chat_count = ('cases_created', 'sum')).reset_index()

In [ ]:
check_count

- KPI computation

In [ ]:
L2_kpi = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                (df_IRT['program'] == "Advertiser Concierge") &
                (~df_IRT['l1_tag'].isnull()) &
                (~df_IRT['l2_tag'].isnull()) &
                (df_IRT['Tenure'] >= 1) &
                (df_IRT['Tenure'] <= 18)].groupby(['l1_tag', 'l2_tag', 'Tenure']).aggregate(
    rr_yes = ('Sum_Res_Yes', 'sum'),
    survey_count = ('Count_Of_Responses', 'sum'),
    THT_chat = ('tht_chat', 'sum'),
    irt_chat_sla = ('irt_chat_sla', 'sum'),
    irt_email_sla = ('irt_email_sla', 'sum')).reset_index()

In [ ]:
chat_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                    (df_IRT['program'] == "Advertiser Concierge") &
                    (df_IRT['case_channel'] == "CHAT") &
                    (~df_IRT['l1_tag'].isnull()) &
                    (~df_IRT['l2_tag'].isnull()) &
                    (df_IRT['Tenure'] >= 1) &
                    (df_IRT['Tenure'] <= 18)].groupby(['l1_tag', 'l2_tag', 'Tenure']).aggregate(
    chat_count = ('cases_created', 'sum')).reset_index()

In [ ]:
email_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                     (df_IRT['program'] == "Advertiser Concierge") &
                     (df_IRT['case_channel'] == "EMAIL") & 
                     (~df_IRT['l1_tag'].isnull()) &
                     (~df_IRT['l2_tag'].isnull()) &
                     (df_IRT['Tenure'] >= 1) &
                     (df_IRT['Tenure'] <= 18)].groupby(['l1_tag', 'l2_tag', 'Tenure']).aggregate(
    email_count = ('cases_created', 'sum')).reset_index()

In [ ]:
L2_kpi = L2_kpi.merge(chat_count, how = "left", on = ['l1_tag', 'l2_tag', 'Tenure'])
L2_kpi = L2_kpi.merge(email_count, how = "left", on = ['l1_tag', 'l2_tag', 'Tenure'])

In [ ]:
L2_kpi['RR'] = L2_kpi['rr_yes']/ L2_kpi['survey_count']
L2_kpi['AHT'] = (L2_kpi['THT_chat']/60)/ L2_kpi['chat_count']
L2_kpi['Chat SLA'] = L2_kpi['irt_chat_sla']/ L2_kpi['chat_count']
L2_kpi['Email SLA'] = L2_kpi['irt_email_sla']/ L2_kpi['email_count']

In [ ]:
L2_kpi.head(10)

- Check Trend

In [ ]:
l1_tags = L2_kpi['l1_tag'].unique()

In [ ]:
L2_trend = pd.DataFrame(columns = ['L1 Tag', 'L2 Tag', 'KPI', 'Volume', 'Trend', 'Statistic', 'pvalue'])

In [ ]:
for i in range(len(l1_tags)):
    l1tag_interest = l1_tags[i]
    l2_tags = check_count[(check_count['l1_tag'] == l1tag_interest) &
                          (check_count['chat_count'] >= 5000)]['l2_tag'].unique()
    
    for j in range(len(l2_tags)):
        l2tag_interest = l2_tags[j]
        
        df_interest = L2_kpi[(L2_kpi['l1_tag'] == l1tag_interest) &
                             (L2_kpi['l2_tag'] == l2tag_interest)]
        df_interest = df_interest.dropna()
        
        for k in range(len(metric)):
            kpi_interest = metric[k]
            if kpi_interest == "RR":
                count = df_interest['survey_count'].sum()
            elif kpi_interest == "Email SLA":
                count = df_interest['email_count'].sum()
            else:
                count = df_interest['chat_count'].sum()
    
            if len(df_interest) >= 5:
                mk_test = mk.original_test(df_interest[kpi_interest])
                trend = mk_test.trend
                zstatistic = mk_test.z
                pvalue = mk_test.p
                L2_trend.loc[len(L2_trend.index)] = [l1tag_interest, l2tag_interest, kpi_interest,
                                                     count, trend, zstatistic, pvalue]
            
            else:
                trend = "Not Applicable"
                zstatistic = "Not Applicable"
                pvalue = "Not Applicable"
                L2_trend.loc[len(L2_trend.index)] = [l1tag_interest, l2tag_interest, kpi_interest,
                                                     count, trend, zstatistic, pvalue]

In [ ]:
L2_trend.loc[(L2_trend['Trend'] == "no trend") &
              (L2_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') < 0) &
              (L2_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "decreasing"

L2_trend.loc[(L2_trend['Trend'] == "no trend") &
              (L2_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') > 0) &
              (L2_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "increasing"

In [ ]:
L2_trend.head(10)

- Get Learning Curve

In [ ]:
L2_learningcurve = pd.DataFrame(columns = ['L1 Tag', 'L2 Tag', 'Metric',
                                           'Volume', 'Average Perfomance', 'Trend', 'Learning Curve'])

In [ ]:
for i in range(len(l1_tags)):
    l1tag_interest = l1_tags[i]
    l2_tags = check_count[(check_count['l1_tag'] == l1tag_interest) &
                          (check_count['chat_count'] >= 5000)]['l2_tag'].unique()
    
    for j in range(len(l2_tags)):
        l2tag_interest = l2_tags[j]
        
        df_interest = L2_kpi[(L2_kpi['l1_tag'] == l1tag_interest) &
                             (L2_kpi['l2_tag'] == l2tag_interest) &
                             (L2_kpi['Tenure'] > 1)]
        df_interest = df_interest.dropna()
        
        for k in range(len(metric)):
            kpi_interest = metric[k]
            if kpi_interest == "RR":
                count = df_interest['survey_count'].sum()
            elif kpi_interest == "Email SLA":
                count = df_interest['email_count'].sum()
            else:
                count = df_interest['chat_count'].sum()
        
            trend = L2_trend.loc[(L2_trend['L1 Tag'] == l1tag_interest) &
                                 (L2_trend['L2 Tag'] == l2tag_interest) &
                                 (L2_trend['KPI'] == kpi_interest), "Trend"].iloc[0]
            team_ave = L2_kpi[kpi_interest].describe()["mean"]
            ave = df_interest[kpi_interest].describe()["mean"]
        
            if ((kpi_interest in increasing_metric) &
                (trend == "increasing")):
            
                curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
                for index in df_interest.index:
                    if df_interest.loc[index, kpi_interest] > team_ave:
                        curve = df_interest.loc[index, 'Tenure']
                        break
                L2_learningcurve.loc[len(L2_learningcurve.index)] = [l1tag_interest, l2tag_interest, kpi_interest,
                                                                     count, ave, trend, curve]
            
            elif ((kpi_interest in decreasing_metric) &
                  (trend == "decreasing")):
            
                curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
                for index in df_interest.index:
                    if df_interest.loc[index, kpi_interest] < ave:
                        curve = df_interest.loc[index, 'Tenure']
                        break
                L2_learningcurve.loc[len(L2_learningcurve.index)] = [l1tag_interest, l2tag_interest, kpi_interest,
                                                                     count, ave, trend, curve]
            
            else:
                L2_learningcurve.loc[len(L2_learningcurve.index)] = [l1tag_interest, l2tag_interest, kpi_interest,
                                                                     count, ave, trend, "Not Applicable"]

In [ ]:
L2_learningcurve.head(10)

In [ ]:
L2_learningcurve.to_csv('../results/All Trends (Top L1 & L2 combinations).csv', index = False)

- KPI Graph

In [ ]:
L2_trend

In [ ]:
kpi_interest = "RR"
L2_trend_interest = L2_trend[L2_trend['KPI'] == kpi_interest]

i,j = 0,0
PLOTS_PER_ROW = 3
fig, ax1 = plt.subplots(math.ceil(len(L2_trend_interest)/PLOTS_PER_ROW),PLOTS_PER_ROW, figsize=(20, 50))

for x in range(len(L2_trend_interest)):
    l1tag_interest = L2_trend_interest.iat[x, 0]
    l2tag_interest = L2_trend_interest.iat[x, 1]

    df_interest = L2_kpi[(L2_kpi['l1_tag'] == l1tag_interest) &
                         (L2_kpi['l2_tag'] == l2tag_interest) &
                         (L2_kpi['Tenure'] > 1)]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    ave = L2_kpi[(L2_kpi['Tenure'] > 1)][kpi_interest].describe()["mean"]
    
    if len(df_interest) >= 5:
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax1[i][j].plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
        ax1[i][j].hlines(y = ave, xmin = df_interest['Tenure'].min(),
                         xmax = df_interest['Tenure'].max(),
                         color = 'orange', linestyle = 'dashed')
        
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['survey_count'])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax2 = ax1[i][j].twinx()
        ax2.plot(X_, Y_, 'gray', linewidth = 2)
        
        target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
        ax1[i][j].hlines(y = target_interest, xmin = 0, xmax = 19,
                         color = 'red', linestyle = 'dashed', label = "Target " + kpi_interest)
        
        curve = L2_learningcurve.loc[(L2_learningcurve['Metric'] == kpi_interest) &
                                     (L2_learningcurve['L1 Tag'] == l1tag_interest) &
                                     (L2_learningcurve['L2 Tag'] == l2tag_interest), 'Learning Curve'].iloc[0]
        if curve != "Not Applicable":
            curve_KPI = df_interest.loc[df_interest['Tenure'] == curve, kpi_interest].iloc[0]
            coords = curve, curve_KPI
            ax1[i][j].annotate("Learning Curve: " + str(curve) + " month",
                               xy = coords, xytext = (10, 15),
                               textcoords = 'offset points', ha = 'left', va = 'bottom',
                               bbox = dict(boxstyle = 'round', pad = 0.5, fc = 'white'))
            ax1[i][j].scatter(curve, curve_KPI, marker = 'o', color = 'orange', s = 80)
        
        plt_title = f"L1 Tag: {l1tag_interest}" + '\n' + f"L2 Tag: {l2tag_interest}"
        ax1[i][j].set_title(label = plt_title, fontweight = "bold", loc = "left", color = "black")
        ax1[i][j].legend(loc = "best")
        ax1[i][j].set_xticks(np.arange(0, 19, 1), minor=False)
        ax1[i][j].set_xlabel("Tenure (in Months)")
        ax2.set_xlabel("Survey Count")
        plt_label = title.loc[(title['KPI'] == kpi_interest), "title"].iloc[0]
        ax1[i][j].set_ylabel(plt_label)
    
    j+=1
    if j%PLOTS_PER_ROW==0:
        i+=1
        j=0
    
plt.tight_layout()
plt.show()

In [ ]:
kpi_interest = "AHT"
L2_trend_interest = L2_trend[L2_trend['KPI'] == kpi_interest]

i,j = 0,0
PLOTS_PER_ROW = 3
fig, ax1 = plt.subplots(math.ceil(len(L2_trend_interest)/PLOTS_PER_ROW),PLOTS_PER_ROW, figsize=(20, 50))

for x in range(len(L2_trend_interest)):
    l1tag_interest = L2_trend_interest.iat[x, 0]
    l2tag_interest = L2_trend_interest.iat[x, 1]


    df_interest = L2_kpi[(L2_kpi['l1_tag'] == l1tag_interest) &
                         (L2_kpi['l2_tag'] == l2tag_interest) &
                         (L2_kpi['Tenure'] > 1)]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    ave = L2_kpi[(L2_kpi['Tenure'] > 1)][kpi_interest].describe()["mean"]
    
    if len(df_interest) >= 5:
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax1[i][j].plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
        ax1[i][j].hlines(y = ave, xmin = df_interest['Tenure'].min(),
                         xmax = df_interest['Tenure'].max(),
                         color = 'orange', linestyle = 'dashed')
        
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['survey_count'])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax2 = ax1[i][j].twinx()
        ax2.plot(X_, Y_, 'gray', linewidth = 2)
        
        target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
        ax1[i][j].hlines(y = target_interest, xmin = 0, xmax = 19,
                         color = 'red', linestyle = 'dashed', label = "Target " + kpi_interest)
        
        curve = L2_learningcurve.loc[(L2_learningcurve['Metric'] == kpi_interest) &
                                     (L2_learningcurve['L1 Tag'] == l1tag_interest) &
                                     (L2_learningcurve['L2 Tag'] == l2tag_interest), 'Learning Curve'].iloc[0]
        if curve != "Not Applicable":
            curve_KPI = df_interest.loc[df_interest['Tenure'] == curve, kpi_interest].iloc[0]
            coords = curve, curve_KPI
            ax1[i][j].annotate("Learning Curve: " + str(curve) + " month",
                               xy = coords, xytext = (10, 15),
                               textcoords = 'offset points', ha = 'left', va = 'bottom',
                               bbox = dict(boxstyle = 'round', pad = 0.5, fc = 'white'))
            ax1[i][j].scatter(curve, curve_KPI, marker = 'o', color = 'orange', s = 80)
        
        plt_title = f"L1 Tag: {l1tag_interest}" + '\n' + f"L2 Tag: {l2tag_interest}"
        ax1[i][j].set_title(label = plt_title, fontweight = "bold", loc = "left", color = "black")
        ax1[i][j].legend(loc = "best")
        ax1[i][j].set_xticks(np.arange(0, 19, 1), minor=False)
        ax1[i][j].set_xlabel("Tenure (in Months)")
        ax2.set_xlabel("Chat Count")
        plt_label = title.loc[(title['KPI'] == kpi_interest), "title"].iloc[0]
        ax1[i][j].set_ylabel(plt_label)
    
    j+=1
    if j%PLOTS_PER_ROW==0:
        i+=1
        j=0
    
plt.tight_layout()
plt.show()

# Learning Curve (L1 & L3 Tag) 

- Check Ticket Count

In [ ]:
check_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                     (df_IRT['program'] == "Advertiser Concierge") &
                     (df_IRT['case_channel'] == "CHAT") &
                     (~df_IRT['l1_tag'].isnull()) &
                     (~df_IRT['l3_tag'].isnull()) &
                     (df_IRT['Tenure'] >= 1) &
                     (df_IRT['Tenure'] <= 18)].groupby(['l1_tag', 'l3_tag']).aggregate(
    chat_count = ('cases_created', 'sum')).reset_index()

In [ ]:
check_count

- KPI computation

In [ ]:
L3_kpi = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                (df_IRT['program'] == "Advertiser Concierge") &
                (~df_IRT['l1_tag'].isnull()) &
                (~df_IRT['l3_tag'].isnull()) &
                (df_IRT['Tenure'] >= 1) &
                (df_IRT['Tenure'] <= 18)].groupby(['l1_tag', 'l3_tag', 'Tenure']).aggregate(
    rr_yes = ('Sum_Res_Yes', 'sum'),
    survey_count = ('Count_Of_Responses', 'sum'),
    THT_chat = ('tht_chat', 'sum'),
    irt_chat_sla = ('irt_chat_sla', 'sum'),
    irt_email_sla = ('irt_email_sla', 'sum')).reset_index()

In [ ]:
chat_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                    (df_IRT['program'] == "Advertiser Concierge") &
                    (df_IRT['case_channel'] == "CHAT") &
                    (~df_IRT['l1_tag'].isnull()) &
                    (~df_IRT['l3_tag'].isnull()) &
                    (df_IRT['Tenure'] >= 1) &
                    (df_IRT['Tenure'] <= 18)].groupby(['l1_tag', 'l3_tag', 'Tenure']).aggregate(
    chat_count = ('cases_created', 'sum')).reset_index()

In [ ]:
email_count = df_IRT[(df_IRT['sbg_gbg(agg)'] == "SBG") &
                     (df_IRT['program'] == "Advertiser Concierge") &
                     (df_IRT['case_channel'] == "EMAIL") & 
                     (~df_IRT['l1_tag'].isnull()) &
                     (~df_IRT['l3_tag'].isnull()) &
                     (df_IRT['Tenure'] >= 1) &
                     (df_IRT['Tenure'] <= 18)].groupby(['l1_tag', 'l3_tag', 'Tenure']).aggregate(
    email_count = ('cases_created', 'sum')).reset_index()

In [ ]:
L3_kpi = L3_kpi.merge(chat_count, how = "left", on = ['l1_tag', 'l3_tag', 'Tenure'])
L3_kpi = L3_kpi.merge(email_count, how = "left", on = ['l1_tag', 'l3_tag', 'Tenure'])

In [ ]:
L3_kpi['RR'] = L3_kpi['rr_yes']/ L3_kpi['survey_count']
L3_kpi['AHT'] = (L3_kpi['THT_chat']/60)/ L3_kpi['chat_count']
L3_kpi['Chat SLA'] = L3_kpi['irt_chat_sla']/ L3_kpi['chat_count']
L3_kpi['Email SLA'] = L3_kpi['irt_email_sla']/ L3_kpi['email_count']

In [ ]:
L3_kpi.head(10)

- Check Trend

In [ ]:
l1_tags = L3_kpi['l1_tag'].unique()

In [ ]:
L3_trend = pd.DataFrame(columns = ['L1 Tag', 'L3 Tag', 'KPI', 'Volume', 'Trend', 'Statistic', 'pvalue'])

In [ ]:
for i in range(len(l1_tags)):
    l1tag_interest = l1_tags[i]
    l3_tags = check_count[(check_count['l1_tag'] == l1tag_interest) &
                          (check_count['chat_count'] >= 5000)]['l3_tag'].unique()
    
    for j in range(len(l3_tags)):
        l3tag_interest = l3_tags[j]
        
        df_interest = L3_kpi[(L3_kpi['l1_tag'] == l1tag_interest) &
                             (L3_kpi['l3_tag'] == l3tag_interest)]
        df_interest = df_interest.dropna()
        
        for k in range(len(metric)):
            kpi_interest = metric[k]
            if kpi_interest == "RR":
                count = df_interest['survey_count'].sum()
            elif kpi_interest == "Email SLA":
                count = df_interest['email_count'].sum()
            else:
                count = df_interest['chat_count'].sum()
    
            if len(df_interest) >= 5:
                mk_test = mk.original_test(df_interest[kpi_interest])
                trend = mk_test.trend
                zstatistic = mk_test.z
                pvalue = mk_test.p
                L3_trend.loc[len(L3_trend.index)] = [l1tag_interest, l3tag_interest, kpi_interest,
                                                     count, trend, zstatistic, pvalue]
            
            else:
                trend = "Not Applicable"
                zstatistic = "Not Applicable"
                pvalue = "Not Applicable"
                L3_trend.loc[len(L3_trend.index)] = [l1tag_interest, l3tag_interest, kpi_interest,
                                                     count, trend, zstatistic, pvalue]

In [ ]:
L3_trend.loc[(L3_trend['Trend'] == "no trend") &
              (L3_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') < 0) &
              (L3_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "decreasing"

L3_trend.loc[(L3_trend['Trend'] == "no trend") &
              (L3_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') > 0) &
              (L3_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "increasing"

In [ ]:
L3_trend.head(10)

- Get Learning Curve

In [ ]:
L3_learningcurve = pd.DataFrame(columns = ['L1 Tag', 'L3 Tag', 'Metric',
                                           'Volume', 'Average Perfomance', 'Trend', 'Learning Curve'])

In [ ]:
for i in range(len(l1_tags)):
    l1tag_interest = l1_tags[i]
    l3_tags = check_count[(check_count['l1_tag'] == l1tag_interest) &
                          (check_count['chat_count'] >= 5000)]['l3_tag'].unique()
    
    for j in range(len(l3_tags)):
        l3tag_interest = l3_tags[j]
        
        df_interest = L3_kpi[(L3_kpi['l1_tag'] == l1tag_interest) &
                             (L3_kpi['l3_tag'] == l3tag_interest) &
                             (L3_kpi['Tenure'] > 1)]
        df_interest = df_interest.dropna()
        
        for k in range(len(metric)):
            kpi_interest = metric[k]
            if kpi_interest == "RR":
                count = df_interest['survey_count'].sum()
            elif kpi_interest == "Email SLA":
                count = df_interest['email_count'].sum()
            else:
                count = df_interest['chat_count'].sum()
        
            trend = L3_trend.loc[(L3_trend['L1 Tag'] == l1tag_interest) &
                                 (L3_trend['L3 Tag'] == l3tag_interest) &
                                 (L3_trend['KPI'] == kpi_interest), "Trend"].iloc[0]
            team_ave = L3_kpi[kpi_interest].describe()["mean"]
            ave = df_interest[kpi_interest].describe()["mean"]
        
            if ((kpi_interest in increasing_metric) &
                (trend == "increasing")):
            
                curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
                for index in df_interest.index:
                    if df_interest.loc[index, kpi_interest] > team_ave:
                        curve = df_interest.loc[index, 'Tenure']
                        break
                L3_learningcurve.loc[len(L3_learningcurve.index)] = [l1tag_interest, l3tag_interest, kpi_interest,
                                                                     count, ave, trend, curve]
            
            elif ((kpi_interest in decreasing_metric) &
                  (trend == "decreasing")):
            
                curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
                for index in df_interest.index:
                    if df_interest.loc[index, kpi_interest] < ave:
                        curve = df_interest.loc[index, 'Tenure']
                        break
                L3_learningcurve.loc[len(L3_learningcurve.index)] = [l1tag_interest, l3tag_interest, kpi_interest,
                                                                     count, ave, trend, curve]
            
            else:
                L3_learningcurve.loc[len(L3_learningcurve.index)] = [l1tag_interest, l3tag_interest, kpi_interest,
                                                                     count, ave, trend, "Not Applicable"]

In [ ]:
L3_learningcurve.head(10)

In [ ]:
L3_learningcurve.to_csv('../results/All Trends (Top L1 & L3 combinations).csv', index = False)

- KPI Graph

In [ ]:
kpi_interest = "RR"
L3_trend_interest = L3_trend[L3_trend['KPI'] == kpi_interest]

i,j = 0,0
PLOTS_PER_ROW = 3
fig, ax1 = plt.subplots(math.ceil(len(L3_trend_interest)/PLOTS_PER_ROW),PLOTS_PER_ROW, figsize=(20, 50))

for x in range(len(L3_trend_interest)):
    l1tag_interest = L3_trend_interest.iat[x, 0]
    l3tag_interest = L3_trend_interest.iat[x, 1]

    df_interest = L3_kpi[(L3_kpi['l1_tag'] == l1tag_interest) &
                         (L3_kpi['l3_tag'] == l3tag_interest) &
                         (L3_kpi['Tenure'] > 1)]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    ave = L3_kpi[(L3_kpi['Tenure'] > 1)][kpi_interest].describe()["mean"]
    
    if len(df_interest) >= 5:
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax1[i][j].plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
        ax1[i][j].hlines(y = ave, xmin = df_interest['Tenure'].min(),
                         xmax = df_interest['Tenure'].max(),
                         color = 'orange', linestyle = 'dashed')
        
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['survey_count'])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax2 = ax1[i][j].twinx()
        ax2.plot(X_, Y_, 'gray', linewidth = 2)
        
        target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
        ax1[i][j].hlines(y = target_interest, xmin = 0, xmax = 19,
                         color = 'red', linestyle = 'dashed', label = "Target " + kpi_interest)
        
        curve = L3_learningcurve.loc[(L3_learningcurve['Metric'] == kpi_interest) &
                                     (L3_learningcurve['L1 Tag'] == l1tag_interest) &
                                     (L3_learningcurve['L3 Tag'] == l3tag_interest), 'Learning Curve'].iloc[0]
        if curve != "Not Applicable":
            curve_KPI = df_interest.loc[df_interest['Tenure'] == curve, kpi_interest].iloc[0]
            coords = curve, curve_KPI
            ax1[i][j].annotate("Learning Curve: " + str(curve) + " month",
                               xy = coords, xytext = (10, 15),
                               textcoords = 'offset points', ha = 'left', va = 'bottom',
                               bbox = dict(boxstyle = 'round', pad = 0.5, fc = 'white'))
            ax1[i][j].scatter(curve, curve_KPI, marker = 'o', color = 'orange', s = 80)
        
        plt_title = f"L1 Tag: {l1tag_interest}" + '\n' + f"L3 Tag: {l3tag_interest}"
        ax1[i][j].set_title(label = plt_title, fontweight = "bold", loc = "left", color = "black")
        ax1[i][j].legend(loc = "best")
        ax1[i][j].set_xticks(np.arange(0, 19, 1), minor=False)
        ax1[i][j].set_xlabel("Tenure (in Months)")
        ax2.set_xlabel("Survey Count")
        plt_label = title.loc[(title['KPI'] == kpi_interest), "title"].iloc[0]
        ax1[i][j].set_ylabel(plt_label)
    
    j+=1
    if j%PLOTS_PER_ROW==0:
        i+=1
        j=0
    
plt.tight_layout()
plt.show()

In [ ]:
kpi_interest = "AHT"
L3_trend_interest = L3_trend[L3_trend['KPI'] == kpi_interest]

i,j = 0,0
PLOTS_PER_ROW = 3
fig, ax1 = plt.subplots(math.ceil(len(L3_trend_interest)/PLOTS_PER_ROW),PLOTS_PER_ROW, figsize=(20, 50))

for x in range(len(L3_trend_interest)):
    l1tag_interest = L3_trend_interest.iat[x, 0]
    l3tag_interest = L3_trend_interest.iat[x, 1]

    df_interest = L3_kpi[(L3_kpi['l1_tag'] == l1tag_interest) &
                         (L3_kpi['l3_tag'] == l3tag_interest) &
                         (L3_kpi['Tenure'] > 1)]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    ave = L3_kpi[(L3_kpi['Tenure'] > 1)][kpi_interest].describe()["mean"]
    
    if len(df_interest) >= 5:
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax1[i][j].plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
        ax1[i][j].hlines(y = ave, xmin = df_interest['Tenure'].min(),
                         xmax = df_interest['Tenure'].max(),
                         color = 'orange', linestyle = 'dashed')
        
        X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['survey_count'])
        X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
        Y_ = X_Y_Spline(X_)
        ax2 = ax1[i][j].twinx()
        ax2.plot(X_, Y_, 'gray', linewidth = 2)
        
        target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
        ax1[i][j].hlines(y = target_interest, xmin = 0, xmax = 19,
                         color = 'red', linestyle = 'dashed', label = "Target " + kpi_interest)
        
        curve = L3_learningcurve.loc[(L3_learningcurve['Metric'] == kpi_interest) &
                                     (L3_learningcurve['L1 Tag'] == l1tag_interest) &
                                     (L3_learningcurve['L3 Tag'] == l3tag_interest), 'Learning Curve'].iloc[0]
        if curve != "Not Applicable":
            curve_KPI = df_interest.loc[df_interest['Tenure'] == curve, kpi_interest].iloc[0]
            coords = curve, curve_KPI
            ax1[i][j].annotate("Learning Curve: " + str(curve) + " month",
                               xy = coords, xytext = (10, 15),
                               textcoords = 'offset points', ha = 'left', va = 'bottom',
                               bbox = dict(boxstyle = 'round', pad = 0.5, fc = 'white'))
            ax1[i][j].scatter(curve, curve_KPI, marker = 'o', color = 'orange', s = 80)
        
        plt_title = f"L1 Tag: {l1tag_interest}" + '\n' + f"L3 Tag: {l3tag_interest}"
        ax1[i][j].set_title(label = plt_title, fontweight = "bold", loc = "left", color = "black")
        ax1[i][j].legend(loc = "best")
        ax1[i][j].set_xticks(np.arange(0, 19, 1), minor=False)
        ax1[i][j].set_xlabel("Tenure (in Months)")
        ax2.set_xlabel("Chat Count")
        plt_label = title.loc[(title['KPI'] == kpi_interest), "title"].iloc[0]
        ax1[i][j].set_ylabel(plt_label)
    
    j+=1
    if j%PLOTS_PER_ROW==0:
        i+=1
        j=0
    
plt.tight_layout()
plt.show()

# Learning Curve (Active Roster) 

from this point, Ben (Subendran Suppiah) asked that it is more insightful to have the tenure computed as their tenure in Production. This will adjust our analysis in how Tenure is computed, and on how we compute the average.

Active Roster Data

In [ ]:
df_active = pd.read_excel('../data/ActiveRoster.xlsx')

In [ ]:
df_active.head(5)

In [ ]:
df_active.shape

In [ ]:
dup = df_active.shape[0] - df_active.drop_duplicates().shape[0]
print(f'There are {dup} duplicate rows')

In [ ]:
df_active['SRTRepID'] = df_active['SRTRepID'].astype('str')

In [ ]:
df_active = df_active[(df_active['LOB'] == "Advertising") &
                      (df_active['Skill'] == "SBG") &
                      (df_active['Position'] == "Client Service Associate") &
                      (df_active['SRTRepID'] != "For Provisioning")]
df_active = df_active[['Employee ID', 'SRTRepID', 'Employee Name', 'Supervisor',
                       'Hired Date', 'Training Start Date', 'Production Date',]]

In [ ]:
active = df_active['SRTRepID'].tolist()

In [ ]:
df_IRT_active = df_IRT

In [ ]:
df_IRT_active = df_IRT_active.merge(df_active[['SRTRepID', 'Production Date']],
                                    how = "left", left_on = 'owner', right_on = 'SRTRepID' )

In [ ]:
df_IRT_active['Production Date'] = pd.to_datetime(df_IRT_active['Production Date'])

In [ ]:
df_IRT_active['Tenure'] = ((df_IRT_active['date_created'] - df_IRT_active['Production Date'])/np.timedelta64(1, 'M'))
df_IRT_active['Tenure'] = np.floor(pd.to_numeric(df_IRT_active['Tenure'], errors='coerce')).astype('Int64') + 1

In [ ]:
df_IRT_active['owner'] = df_IRT_active['owner'].astype('str')

- KPI computation

In [ ]:
kpi = df_IRT_active[(df_IRT_active['sbg_gbg(agg)'] == "SBG") &
             (df_IRT_active['program'] == "Advertiser Concierge") &
             (df_IRT_active['owner'].isin(active))&
             (df_IRT_active['Tenure'] >= 1) &
             (df_IRT_active['Tenure'] <= 18)].groupby(['Tenure']).aggregate(
    rr_yes = ('Sum_Res_Yes', 'sum'),
    survey_count = ('Count_Of_Responses', 'sum'),
    THT_chat = ('tht_chat', 'sum'),
    irt_chat_sla = ('irt_chat_sla', 'sum'),
    irt_email_sla = ('irt_email_sla', 'sum'),
    agent_count = ('owner', 'nunique')).reset_index()

In [ ]:
chat_count = df_IRT_active[(df_IRT_active['sbg_gbg(agg)'] == "SBG") &
                    (df_IRT_active['program'] == "Advertiser Concierge") &
                    (df_IRT_active['owner'].isin(active))&
                    (df_IRT_active['case_channel'] == "CHAT") &
                    (df_IRT_active['Tenure'] >= 1) &
                    (df_IRT_active['Tenure'] <= 18)].groupby(['Tenure']).aggregate(
    chat_count = ('cases_created', 'sum')).reset_index()

In [ ]:
email_count = df_IRT_active[(df_IRT_active['sbg_gbg(agg)'] == "SBG") &
                     (df_IRT_active['program'] == "Advertiser Concierge") &
                     (df_IRT_active['owner'].isin(active))&
                     (df_IRT_active['case_channel'] == "EMAIL") &
                     (df_IRT_active['Tenure'] >= 1) &
                     (df_IRT_active['Tenure'] <= 18)].groupby(['Tenure']).aggregate(
    email_count = ('cases_created', 'sum')).reset_index()

In [ ]:
kpi = kpi.merge(chat_count, how = "left", on = "Tenure")
kpi = kpi.merge(email_count, how = "left", on = "Tenure")

In [ ]:
kpi['RR'] = kpi['rr_yes']/ kpi['survey_count']
kpi['AHT'] = (kpi['THT_chat']/60)/ kpi['chat_count']
kpi['Chat SLA'] = kpi['irt_chat_sla']/ kpi['chat_count']
kpi['Email SLA'] = kpi['irt_email_sla']/ kpi['email_count']

In [ ]:
# active_verification = kpi[['Tenure', 'agent_count', 'survey_count', 'chat_count', 'email_count']]

In [ ]:
# active_verification.to_csv('../results/Data Verification (Survey and Ticket count).csv', index = False)

- Check Trend

In [ ]:
kpi_trend = pd.DataFrame(columns = ['KPI', 'Volume', 'Trend', 'Statistic', 'pvalue'])

In [ ]:
for i in range(len(metric)):
    kpi_interest = metric[i]
    
    if kpi_interest == "RR":
        df_interest = kpi[['Tenure', 'survey_count', kpi_interest]]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        count = df_interest['survey_count'].sum()
        
        mk_test = mk.original_test(df_interest[kpi_interest])
        trend = mk_test.trend
        zstatistic = mk_test.z
        pvalue = mk_test.p
        kpi_trend.loc[len(kpi_trend.index)] = [kpi_interest, count, trend, zstatistic, pvalue]
    
    elif kpi_interest == "Email SLA":
        df_interest = kpi[['Tenure', 'email_count', kpi_interest]]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        count = df_interest['email_count'].sum()
        
        mk_test = mk.original_test(df_interest[kpi_interest])
        trend = mk_test.trend
        zstatistic = mk_test.z
        pvalue = mk_test.p
        kpi_trend.loc[len(kpi_trend.index)] = [kpi_interest, count, trend, zstatistic, pvalue]
            
    else:
        df_interest = kpi[['Tenure', 'chat_count', kpi_interest]]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        count = df_interest['chat_count'].sum()
        
        mk_test = mk.original_test(df_interest[kpi_interest])
        trend = mk_test.trend
        zstatistic = mk_test.z
        pvalue = mk_test.p
        kpi_trend.loc[len(kpi_trend.index)] = [kpi_interest, count, trend, zstatistic, pvalue]

In [ ]:
kpi_trend.loc[(kpi_trend['Trend'] == "no trend") &
              (kpi_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') < 0) &
              (kpi_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "decreasing"

kpi_trend.loc[(kpi_trend['Trend'] == "no trend") &
              (kpi_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') > 0) &
              (kpi_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "increasing"

In [ ]:
kpi_trend

- Get Learning Curve

In [ ]:
KPI_learningcurve = pd.DataFrame(columns = ['Metric', 'Volume', 'Average Perfomance', 'Trend', 'Learning Curve'])

In [ ]:
for i in range(len(metric)):
    kpi_interest = metric[i]
    df_interest = kpi
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        
    if kpi_interest == "RR":
        count = df_interest['survey_count'].sum()
    elif kpi_interest == "Email SLA":
        count = df_interest['email_count'].sum()
    else:
        count = df_interest['chat_count'].sum()
        
    df_interest = df_interest[['Tenure', kpi_interest]]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    
    trend = kpi_trend.loc[(kpi_trend['KPI'] == kpi_interest), "Trend"].iloc[0]
    ave = df_interest[kpi_interest].describe()["mean"]
        
    if ((kpi_interest in increasing_metric) &
        (trend == "increasing")):
        
        curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
        for index in df_interest.index:
            if df_interest.loc[index, kpi_interest] > ave:
                curve = df_interest.loc[index, 'Tenure']
                break
        
        KPI_learningcurve.loc[len(KPI_learningcurve.index)] = [kpi_interest, count, ave, trend, curve]
            
    elif ((kpi_interest in decreasing_metric) &
          (trend == "decreasing")):
        
        curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
        for index in df_interest.index:
            if df_interest.loc[index, kpi_interest] < ave:
                curve = df_interest.loc[index, 'Tenure']
                break
        KPI_learningcurve.loc[len(KPI_learningcurve.index)] = [kpi_interest, count, ave, trend, curve]
            
    else:
        KPI_learningcurve.loc[len(KPI_learningcurve.index)] = [kpi_interest, count, ave, trend, "Not Applicable"]

In [ ]:
KPI_learningcurve

- KPI Graph

In [ ]:
kpi_interest = "RR"
df_interest = kpi[['Tenure', 'survey_count', kpi_interest]]
df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    
fig, ax1 = plt.subplots(figsize = (8, 5))
target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
ave = df_interest[kpi_interest].describe()["mean"]

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax1.plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
ax1.set_xlabel("Tenure (in Months)")
ax1.set_ylabel("Resolution Rate")

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['survey_count'])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax2 = ax1.twinx()
ax2.plot(X_, Y_, 'gray', linewidth = 2)
ax2.set_ylabel("Survey Count")

curve = KPI_learningcurve.loc[(KPI_learningcurve['Metric'] == kpi_interest), 'Learning Curve'].iloc[0]
if curve != "Not Applicable":
    curve_KPI = df_interest.loc[df_interest['Tenure'] == curve, kpi_interest].iloc[0]
    coords = curve, curve_KPI
    ax1.annotate("Learning Curve: " + str(curve) + " month",
                 xy = coords, xytext = (10, 15),
                 textcoords = 'offset points', ha = 'left', va = 'bottom',
                 bbox = dict(boxstyle = 'round', pad = 0.5, fc = 'white'))
    ax1.scatter(curve, curve_KPI, marker = 'o', color = 'orange', s = 80)

ax1.hlines(y = target_interest, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'red', linestyle = 'dashed', label = "Target")
ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'black', linestyle = 'dashed', label = "Mean")

ax1.set_title(label = "Resolution Rate", fontweight = "bold", loc = "left", color = "black")
ax1.legend(loc = "lower right")
ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        
plt.show()

In [ ]:
kpi_interest = "AHT"
df_interest = kpi[['Tenure', 'chat_count', kpi_interest]]
df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    
fig, ax1 = plt.subplots(figsize = (8, 5))
target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
ave = df_interest[kpi_interest].describe()["mean"]

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest[kpi_interest])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax1.plot(X_, Y_, 'orange', linewidth = 2, label = kpi_interest)
ax1.set_xlabel("Tenure (in Months)")
ax1.set_ylabel("Resolution Rate")

X_Y_Spline = make_interp_spline(df_interest['Tenure'], df_interest['chat_count'])
X_ = np.linspace(df_interest['Tenure'].min(), df_interest['Tenure'].max(), 500)
Y_ = X_Y_Spline(X_)
ax2 = ax1.twinx()
ax2.plot(X_, Y_, 'gray', linewidth = 2)
ax2.set_ylabel("Chat Count")

ax1.hlines(y = target_interest, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'red', linestyle = 'dashed', label = "Target")
ax1.hlines(y = ave, xmin = df_interest['Tenure'].min(),
           xmax = df_interest['Tenure'].max(),
           color = 'black', linestyle = 'dashed', label = "Mean")

curve = KPI_learningcurve.loc[(KPI_learningcurve['Metric'] == kpi_interest), 'Learning Curve'].iloc[0]
if curve != "Not Applicable":
    curve_KPI = df_interest.loc[df_interest['Tenure'] == curve, kpi_interest].iloc[0]
    coords = curve, curve_KPI
    ax1.annotate("Learning Curve: " + str(curve) + " month",
                 xy = coords, xytext = (10, 15),
                 textcoords = 'offset points', ha = 'left', va = 'bottom',
                 bbox = dict(boxstyle = 'round', pad = 0.5, fc = 'white'))
    ax1.scatter(curve, curve_KPI, marker = 'o', color = 'orange', s = 80)

ax1.set_title(label = "Average Handle Time (Chat)", fontweight = "bold", loc = "left", color = "black")
ax1.legend(loc = "lower right")
ax1.set_xticks(np.arange(0, 19, 1), minor=False)
        
plt.show()

# Learning Curve (Individual) 

- KPI computation

In [ ]:
indiv_kpi = df_IRT_active[(df_IRT_active['sbg_gbg(agg)'] == "SBG") &
             (df_IRT_active['program'] == "Advertiser Concierge") &
             (df_IRT_active['owner'].isin(active))&
             (df_IRT_active['Tenure'] >= 1) &
             (df_IRT_active['Tenure'] <= 18)].groupby(['owner', 'Tenure']).aggregate(
    rr_yes = ('Sum_Res_Yes', 'sum'),
    survey_count = ('Count_Of_Responses', 'sum'),
    THT_chat = ('tht_chat', 'sum'),
    irt_chat_sla = ('irt_chat_sla', 'sum'),
    irt_email_sla = ('irt_email_sla', 'sum')).reset_index()

In [ ]:
chat_count = df_IRT_active[(df_IRT_active['sbg_gbg(agg)'] == "SBG") &
                    (df_IRT_active['program'] == "Advertiser Concierge") &
                    (df_IRT_active['owner'].isin(active))&
                    (df_IRT_active['case_channel'] == "CHAT") &
                    (df_IRT_active['Tenure'] >= 1) &
                    (df_IRT_active['Tenure'] <= 18)].groupby(['owner', 'Tenure']).aggregate(
    chat_count = ('cases_created', 'sum')).reset_index()

In [ ]:
email_count = df_IRT_active[(df_IRT_active['sbg_gbg(agg)'] == "SBG") &
                     (df_IRT_active['program'] == "Advertiser Concierge") &
                     (df_IRT_active['owner'].isin(active))&
                     (df_IRT_active['case_channel'] == "EMAIL") &
                     (df_IRT_active['Tenure'] >= 1) &
                     (df_IRT_active['Tenure'] <= 18)].groupby(['owner', 'Tenure']).aggregate(
    email_count = ('cases_created', 'sum')).reset_index()

In [ ]:
indiv_kpi = indiv_kpi.merge(chat_count, how = "left", on = ['owner', 'Tenure'])
indiv_kpi = indiv_kpi.merge(email_count, how = "left", on = ['owner', 'Tenure'])

In [ ]:
indiv_kpi['RR'] = indiv_kpi['rr_yes']/ indiv_kpi['survey_count']
indiv_kpi['AHT'] = (indiv_kpi['THT_chat']/60)/ indiv_kpi['chat_count']
indiv_kpi['Chat SLA'] = indiv_kpi['irt_chat_sla']/ indiv_kpi['chat_count']
indiv_kpi['Email SLA'] = indiv_kpi['irt_email_sla']/ indiv_kpi['email_count']

In [ ]:
indiv_kpi.to_csv('../results/Individual KPI (Active Agents).csv', index = False)

- Check Trend

In [ ]:
indiv_trend = pd.DataFrame(columns = ['Owner', 'Metric', 'Volume', 'Trend', 'Statistic', 'pvalue'])

In [ ]:
for i in range(len(active)):
    for j in range(len(metric)):
        owner_interest = active[i]
        kpi_interest = metric[j]
        df_interest = indiv_kpi[indiv_kpi['owner'] == owner_interest]
        
        if kpi_interest == "RR":
            count = df_interest['survey_count'].sum()
        elif kpi_interest == "Email SLA":
            count = df_interest['email_count'].sum()
        else:
            count = df_interest['chat_count'].sum()
            
        df_interest = df_interest[['Tenure', kpi_interest]]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    
        if len(df_interest) >= 5:
            mk_test = mk.original_test(df_interest[kpi_interest])
            trend = mk_test.trend
            zstatistic = mk_test.z
            pvalue = mk_test.p
            indiv_trend.loc[len(indiv_trend.index)] = [owner_interest, kpi_interest, count,
                                                 trend, zstatistic, pvalue]
            
        else:
            trend = "Not Applicable"
            zstatistic = "Not Applicable"
            pvalue = "Not Applicable"
            indiv_trend.loc[len(indiv_trend.index)] = [owner_interest, kpi_interest, count,
                                                 trend, zstatistic, pvalue]

In [ ]:
indiv_trend.loc[(indiv_trend['Trend'] == "no trend") &
              (indiv_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') < 0) &
              (indiv_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "decreasing"

indiv_trend.loc[(indiv_trend['Trend'] == "no trend") &
              (indiv_trend['Statistic'].apply(pd.to_numeric, errors = 'coerce') > 0) &
              (indiv_trend['pvalue'].apply(pd.to_numeric, errors = 'coerce') < 0.15),
              'Trend'] = "increasing"

In [ ]:
for i in range(len(metric)):
    
    kpi_interest = metric[i]
    
    summary = indiv_trend[indiv_trend['Metric'] == kpi_interest].groupby('Trend').aggregate(
        count = ('Trend', 'count')).reset_index().sort_values(['count'], ascending = True)
    
    fig, ax = plt.subplots(figsize=(8, 5))
    g = ax.barh(summary['Trend'], summary['count'], color = "orange")
    ax.set_title(label = kpi_interest, fontweight = "bold", loc = "left", color = "black")
    ax.set_xlabel("Count")
    ax.set_ylabel("Trend")
    ax.bar_label(g, label_type="edge", fontweight = "bold")
    plt.show()
    
    summary['count_%'] = round((summary['count'] / summary['count'].sum()) * 100, 2)
    print(summary.sort_values(['count'], ascending = False))
    

- Get Learning Curve

In [ ]:
indiv_learningcurve = pd.DataFrame(columns = ['Owner', 'Metric', 'Volume', 'Average Perfomance', 'Trend', 'Learning Curve'])

In [ ]:
for i in range(len(active)):
    for j in range(len(metric)):
        owner_interest = active[i]
        kpi_interest = metric[j]
        
        df_interest = indiv_kpi[(indiv_kpi['owner'] == owner_interest)]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        
        if kpi_interest == "RR":
            count = df_interest['survey_count'].sum()
        elif kpi_interest == "Email SLA":
            count = df_interest['email_count'].sum()
        else:
            count = df_interest['chat_count'].sum()
        
        df_interest = df_interest[['Tenure', kpi_interest]]
        df_interest = df_interest[~(df_interest[kpi_interest].isna())]
        
        trend = indiv_trend.loc[(indiv_trend['Owner'] == owner_interest) &
                             (indiv_trend['Metric'] == kpi_interest), "Trend"].iloc[0]
        team_ave = indiv_kpi[kpi_interest].describe()["mean"]
        ave = df_interest[kpi_interest].describe()["mean"]
        
        if ((kpi_interest in increasing_metric) &
            (trend == "increasing")):
            
            curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
            for index in df_interest.index:
                if df_interest.loc[index, kpi_interest] > team_ave:
                    curve = df_interest.loc[index, 'Tenure']
                    break
            indiv_learningcurve.loc[len(indiv_learningcurve.index)] = [owner_interest, kpi_interest, count,
                                                                 ave, trend, curve]
            
        elif ((kpi_interest in decreasing_metric) &
              (trend == "decreasing")):
            
            curve = df_interest.loc[(df_interest.index).min(), 'Tenure']
            for index in df_interest.index:
                if df_interest.loc[index, kpi_interest] < ave:
                    curve = df_interest.loc[index, 'Tenure']
                    break
            indiv_learningcurve.loc[len(indiv_learningcurve.index)] = [owner_interest, kpi_interest, count,
                                                                 ave, trend, curve]
            
        else:
            indiv_learningcurve.loc[len(indiv_learningcurve.index)] = [owner_interest, kpi_interest, count,
                                                                 ave, trend, "Not Applicable"]

In [ ]:
indiv_learningcurve.to_csv('../results/All Trends (Active Agents).csv', index = False)

- Creating RR Cluster

In [ ]:
rr_group = indiv_learningcurve[indiv_learningcurve['Metric'] == "RR"]

In [ ]:
rr_breaks = jenkspy.jenks_breaks(rr_group[~(rr_group['Average Perfomance'].isna())]['Average Perfomance'],
                                   n_classes = 3)
rr_group['Performance Group'] = pd.cut(rr_group['Average Perfomance'],
                                         bins = rr_breaks,
                                         labels = ['Low', 'Medium', 'High'],
                                         include_lowest = True)
rr_group['Performance Group'] = (rr_group['Performance Group'].cat
                                   .add_categories('Not Applicable')
                                   .fillna('Not Applicable'))

In [ ]:
check = rr_group.groupby('Performance Group').aggregate(
    count = ('Performance Group', 'count'),
    ave_perf = ('Average Perfomance', 'mean')).reset_index().sort_values(['count'], ascending = True)
check['count_%'] = round((check['count'] / check['count'].sum()) * 100, 2)
check.sort_values(['count'], ascending = False)

In [ ]:
# Cluster 1 - Right Trend & High Mean
# Cluster 2 - Right Trend & Medium Mean
# Cluster 3 - Right Trend & Low Mean
# Cluster 4 - No Trend & High Mean
# Cluster 5 - No Trend & Medium Mean
# Cluster 6 - No Trend & Low Mean
# Cluster 7 - Wrong Trend
# Cluster 8 - Not Applicable

In [ ]:
rr_group.loc[(rr_group['Trend'] == "increasing") &
             (rr_group['Performance Group'] == "High"), 'Cluster'] = "Cluster 01"
rr_group.loc[(rr_group['Trend'] == "increasing") &
             (rr_group['Performance Group'] == "Medium"), 'Cluster'] = "Cluster 02"
rr_group.loc[(rr_group['Trend'] == "increasing") &
             (rr_group['Performance Group'] == "Low"), 'Cluster'] = "Cluster 03"
rr_group.loc[(rr_group['Trend'] == "no trend") &
             (rr_group['Performance Group'] == "High"), 'Cluster'] = "Cluster 04"
rr_group.loc[(rr_group['Trend'] == "no trend") &
             (rr_group['Performance Group'] == "Medium"), 'Cluster'] = "Cluster 05"
rr_group.loc[(rr_group['Trend'] == "no trend") &
             (rr_group['Performance Group'] == "Low"), 'Cluster'] = "Cluster 06"
rr_group.loc[(rr_group['Trend'] == "decreasing"), 'Cluster'] = "Cluster 07"
rr_group['Cluster'].fillna("Cluster 08", inplace = True)

In [ ]:
summary = rr_group.groupby('Cluster').aggregate(
    count = ('Cluster', 'count')).reset_index().sort_values(['count'], ascending = True)
    
fig, ax = plt.subplots(figsize=(8, 5))
g = ax.barh(summary['Cluster'], summary['count'], color = "orange")
ax.set_title(label = "Resolution Rate", fontweight = "bold", loc = "left", color = "black")
ax.set_xlabel("Count")
ax.set_ylabel("Trend Clusters")
ax.bar_label(g, label_type="edge", fontweight = "bold")
plt.show()
    
summary['count_%'] = round((summary['count'] / summary['count'].sum()) * 100, 2)
print(summary.sort_values(['count'], ascending = False))

For RR output

Ben asked when does the agent first met the 71% RR Target.

In [ ]:
indiv_rrcurve = pd.DataFrame(columns = ['Owner', 'RR Curve'])

In [ ]:
for i in range(len(active)):
    owner_interest = active[i]
    kpi_interest = "RR"
    
    df_interest = indiv_kpi[(indiv_kpi['owner'] == owner_interest)]
    df_interest = df_interest[~(df_interest[kpi_interest].isna())]
    df_interest = df_interest[['Tenure', kpi_interest]]
    target_interest = target.loc[(target['KPI'] == kpi_interest), "target"].iloc[0]
        
    curve = ""
    for index in df_interest.index:
        if df_interest.loc[index, kpi_interest] >= target_interest:
            curve = df_interest.loc[index, 'Tenure']
            break
    indiv_rrcurve.loc[len(indiv_rrcurve.index)] = [owner_interest, curve]

In [ ]:
indiv_rrcurve.loc[indiv_rrcurve['RR Curve'] == "", "RR Curve"] = "Not Applicable"

In [ ]:
rr_group = rr_group.merge(df_active, how = "left", left_on = "Owner", right_on = "SRTRepID")

In [ ]:
rr_group = rr_group.merge(indiv_rrcurve, how = "left", on = "Owner")

In [ ]:
rr_group['Hired Date'] = pd.to_datetime(rr_group['Hired Date'])
rr_group['Production Date'] = pd.to_datetime(rr_group['Hired Date'])
rr_group['Today'] = datetime.date.today()
rr_group['Today'] = pd.to_datetime(rr_group['Today'])

In [ ]:
rr_group['Overall Tenure'] = ((rr_group['Today'] - rr_group['Hired Date'])/np.timedelta64(1, 'M'))
rr_group['Overall Tenure'] = np.floor(pd.to_numeric(rr_group['Overall Tenure'], errors='coerce')).astype('Int64')

In [ ]:
rr_group['Production Tenure'] = ((rr_group['Today'] - rr_group['Production Date'])/np.timedelta64(1, 'M'))
rr_group['Production Tenure'] = np.floor(pd.to_numeric(rr_group['Production Tenure'], errors='coerce')).astype('Int64')

In [ ]:
rr_group.loc[rr_group['Average Perfomance'] >= 0.71, 'Reach Target'] = "Yes"
rr_group.loc[rr_group['Average Perfomance'] < 0.71, 'Reach Target'] = "No"

In [ ]:
rr_group = rr_group[['Employee ID', 'SRTRepID', 'Employee Name', 'Supervisor',
                     'Hired Date', 'Training Start Date', 'Production Date',
                     'Metric', 'Volume', 'Average Perfomance', 'Reach Target',
                     'Trend', 'Learning Curve', 'Performance Group', 'Cluster', 'RR Curve']]

In [ ]:
rr_group.to_csv('../results/RR Trend (Active Agents).csv', index = False)